In [1]:
from sklearn.tree import DecisionTreeClassifier
import pandas as pd
import numpy as np
import json
from Tree import Tree

In [2]:
with open('games.json') as f:
    data_json = json.load(f)
champions = set()
for game in data_json:
    for player in game:
        for champion in player:
            champion_name = champion[0]
            if champion_name:
                champions.add(champion_name)
champions = list(champions)

In [3]:
df = pd.DataFrame(columns=champions+['target'], dtype=np.int8)
for i, game in enumerate(data_json):
    winner, loser = game[0], game[1]
    winner_champs = [c[0] for c in winner]
    loser_champs  = [c[0] for c in loser]
    winner_row = np.empty(len(champions)+1, dtype=np.str)
    loser_row  = np.empty(len(champions)+1, dtype=np.str)
    winner_row.fill('f')
    loser_row.fill('f')
    winner_row[-1] = 1
    loser_row[-1] = 0
    for j, champion in enumerate(champions):
        if champion in winner_champs:
            winner_row[j] = 't'
        if champion in loser_champs:
            loser_row[j]  = 't'
    df.loc[2*i]   = winner_row
    df.loc[2*i+1] = loser_row
df.head()

Nami Leblanc KogMaw Lux Skarner Malzahar Zed Nasus Qiyana Volibear  ...  \
0    t       f      f   f       f        f   f     f      f        f  ...   
1    f       t      f   f       f        f   f     f      f        f  ...   
2    f       f      f   f       f        f   f     f      f        t  ...   
3    t       f      f   f       f        f   f     f      f        f  ...   
4    t       f      f   t       f        f   f     f      f        f  ...   

  Annie RekSai Nocturne Ornn Sion Vayne Varus Maokai Jax target  
0     t      f        f    f    f     f     f      f   f      1  
1     f      f        f    f    f     f     f      f   f      0  
2     f      f        f    f    t     f     f      f   t      1  
3     f      f        f    f    f     f     f      f   f      0  
4     t      f        f    f    f     f     f      f   f      1  

[5 rows x 53 columns]

In [4]:
train = df.sample(frac=0.8)
test  = df.drop(train.index)
X_train = train.drop('target', axis=1)
X_test  =  test.drop('target', axis=1)
Y_train = train.target
Y_test  =  test.target 

In [5]:
tree = Tree(train)

In [6]:
tree.draw()

In [16]:
Y_predict = [tree.classify(X_test.iloc[i]) for i in range(len(X_test))]

In [24]:
Y_predict = pd.Series(Y_predict)
Y_predict.index = Y_test.index
good = Y_predict==Y_test
good.value_counts()

False    736
True     704
dtype: int64

In [ ]:
tree = DecisionTreeClassifier(criterion='entropy', min_samples_leaf=5)
tree.fit(X_train, Y_train)
tree.score(X_train, Y_train)

In [ ]:
tree.score(X_test, Y_test)

In [ ]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Input, Dense, Dropout, BatchNormalization

In [ ]:
model = Sequential([
    Input(52),
    Dense(128),
    Dense(128),
#     Dropout(0.4),
#     Dense(640),
#     Dropout(0.4),
    Dense(1)
])
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

In [ ]:
model.fit(X_train, Y_train, epochs=20)

In [ ]:
n_nodes = tree.tree_.node_count
children_left = tree.tree_.children_left
children_right = tree.tree_.children_right
feature = tree.tree_.feature

node_depth = np.zeros(shape=n_nodes, dtype=np.int64)
is_leaves = np.zeros(shape=n_nodes, dtype=bool)
winrate = np.zeros(shape=n_nodes, dtype=np.float32)

stack = [(0, -1)]
while len(stack) > 0:
    node_id, parent_depth = stack.pop()
    node_depth[node_id] = parent_depth + 1

    # If we have a test node
    if (children_left[node_id] != children_right[node_id]):
        stack.append((children_left[node_id], parent_depth + 1))
        stack.append((children_right[node_id], parent_depth + 1))
    else:
        is_leaves[node_id] = True

# First let's retrieve the decision path of each sample. The decision_path
# method allows to retrieve the node indicator functions. A non zero element of
# indicator matrix at the position (i, j) indicates that the sample i goes
# through the node j.

node_indicator = tree.decision_path(X_train)

leave_id = tree.apply(X_train)

sample_id = 0
node_index = node_indicator.indices[node_indicator.indptr[sample_id]:
                                    node_indicator.indptr[sample_id + 1]]

print('Rules used to predict sample %s: ' % sample_id)
for node_id in node_index:
    if leave_id[sample_id] == node_id:
        continue

    if (X_train[sample_id, feature[node_id]] <= threshold[node_id]):
        threshold_sign = "<="
    else:
        threshold_sign = ">"

    print("decision id node %s : (X_train[%s, %s] (= %s) %s %s)"
          % (node_id,
             sample_id,
             feature[node_id],
             X_train[sample_id, feature[node_id]],
             threshold_sign,
             threshold[node_id]))